<a href="https://colab.research.google.com/github/francesca-leonardi/Learning-Machine-Learning/blob/main/drug_classification.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [2]:
### Simple logistic regression ###

import numpy as np
import pandas as pd
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import accuracy_score, precision_score, recall_score, confusion_matrix
from sklearn.model_selection import train_test_split
from scipy.sparse import csr_matrix

df = pd.read_csv('/content/drug200.csv')

# Conversion of non numerical data in the dataframe to numerical data

df.Sex = df.Sex.apply(lambda p: 0 if p == 'M' else 1)
df.BP = df.BP.apply(lambda p: 0 if p == 'NORMAL' else (-1 if p == 'LOW' else 1))
df.Cholesterol = df.Cholesterol.apply(lambda p: 0 if p == 'NORMAL' else 1)

def convertor(row,values):
  i = 0
  while row != values[i]:
    i += 1
  return i

drug_values = df.Drug.unique()
df.Drug = df.Drug.apply(lambda x: convertor(x,drug_values))

# Preparation of the training and testing set

train, test = train_test_split(df, train_size=0.8, random_state=42)

X_train = train.iloc[:,:-1]
y_train = train.iloc[:,-1].tolist()

X_test = test.iloc[:,:-1]
y_test = test.iloc[:,-1].tolist()

# Training of the model and prediction

model = LogisticRegression(multi_class='multinomial', max_iter = 5000)

model.fit(X_train,y_train)

y_hat = model.predict(X_test)

# Performance of the model

accuracy = accuracy_score(y_true = y_test, y_pred=y_hat)

cm = confusion_matrix(y_true = y_test, y_pred = y_hat)

print("Accuracy score:",accuracy)
print("Confusion matrix:\n",cm)
print("Drugs:",drug_values)

/usr/local/lib/python3.12/dist-packages/sklearn/linear_model/_logistic.py:1247: FutureWarning: 'multi_class' was deprecated in version 1.5 and will be removed in 1.7. From then on, it will always use 'multinomial'. Leave it to its default value to avoid this warning.
  warnings.warn(


Accuracy score: 0.9
Confusion matrix:
 [[15  0  0  0  0]
 [ 0  1  4  0  0]
 [ 0  0 11  0  0]
 [ 0  0  0  6  0]
 [ 0  0  0  0  3]]
Drugs: ['DrugY' 'drugC' 'drugX' 'drugA' 'drugB']


In [5]:
### Neural network softmax classification ###

import numpy as np
import tensorflow as tf
from tensorflow import keras
from keras import layers

train, test = train_test_split(df, train_size=0.8, random_state=42)
train, cv = train_test_split(train, train_size=0.75)

X_train = train.iloc[:,:-1]
y_train = train.iloc[:,-1].tolist()

X_cv = cv.iloc[:,:-1]
y_cv = cv.iloc[:,-1].tolist()

X_test = test.iloc[:,:-1]
y_test = test.iloc[:,-1].tolist()

output_size = len(drug_values)
input_size = X_train.shape[1]

first_layer = range(20,31)
second_layer = range(5,16)
N = len(first_layer)*len(second_layer)
q1 = (N//4)+1
q2 = (N//2)+1
q3 = (3*N//4)+1
q4 = N
counter = 0

print(f"Training of {N} models")

accuracy = []

for n1 in first_layer:
  for n2 in second_layer:

    counter += 1
    print(f'MODEL {counter}/{N}')

    model = keras.Sequential([layers.Dense(n1,activation = "relu", input_shape=(input_size,)),
                              layers.Dense(n2,activation = "relu"),
                              layers.Dense(output_size,activation = "softmax")])

    model.compile(optimizer="adam",loss="sparse_categorical_crossentropy")

    X_train = np.array(X_train)
    X_cv = np.array(X_cv)
    y_train = np.array(y_train)
    y_cv = np.array(y_cv)

    history = model.fit(X_train,y_train,epochs=400,batch_size=64)

    if counter == q1:
      print('________________________________________________________________\n\n\t25% down, 75% to go. Drink a shot, you earned it!\n________________________________________________________________')
    if counter == q2:
      print('_____________________________________________________________________\n\n\tYou are halfway through it! Go celebrate, get a shot!\n_____________________________________________________________________')
    if counter == q3:
      print('________________________________________________________________________________________\n\n\tAlmost there, only 25% of models are missing! Hold on, chunk that shot!\n________________________________________________________________________________________')
    if counter == q4:
      print("YOU MADE IT! Let's raise a glass!")

    y_tilde = model.predict(X_cv)
    y_guess = np.argmax(y_tilde,axis=1)

    acc = accuracy_score(y_cv,y_guess)
    accuracy.append([n1,n2,acc])

print(sorted(accuracy, key = lambda x: x[2], reverse=True))

Training of 121 models
MODEL 1/121
Epoch 1/400


/usr/local/lib/python3.12/dist-packages/keras/src/layers/core/dense.py:93: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(activity_regularizer=activity_regularizer, **kwargs)


2/2 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - loss: 11.8006 
Epoch 2/400
2/2 ━━━━━━━━━━━━━━━━━━━━ 0s 22ms/step - loss: 11.1446
Epoch 3/400
2/2 ━━━━━━━━━━━━━━━━━━━━ 0s 27ms/step - loss: 10.1763
Epoch 4/400
2/2 ━━━━━━━━━━━━━━━━━━━━ 0s 22ms/step - loss: 9.8635
Epoch 5/400
2/2 ━━━━━━━━━━━━━━━━━━━━ 0s 22ms/step - loss: 9.8234 
Epoch 6/400
2/2 ━━━━━━━━━━━━━━━━━━━━ 0s 23ms/step - loss: 9.1894
Epoch 7/400
2/2 ━━━━━━━━━━━━━━━━━━━━ 0s 22ms/step - loss: 8.7289
Epoch 8/400
2/2 ━━━━━━━━━━━━━━━━━━━━ 0s 24ms/step - loss: 8.0113
Epoch 9/400
2/2 ━━━━━━━━━━━━━━━━━━━━ 0s 23ms/step - loss: 7.5081
Epoch 10/400
2/2 ━━━━━━━━━━━━━━━━━━━━ 0s 24ms/step - loss: 7.3370
Epoch 11/400
2/2 ━━━━━━━━━━━━━━━━━━━━ 0s 24ms/step - loss: 6.7475
Epoch 12/400
2/2 ━━━━━━━━━━━━━━━━━━━━ 0s 25ms/step - loss: 6.3092
Epoch 13/400
2/2 ━━━━━━━━━━━━━━━━━━━━ 0s 23ms/step - loss: 5.8694
Epoch 14/400
2/2 ━━━━━━━━━━━━━━━━━━━━ 0s 23ms/step - loss: 5.6635
Epoch 15/400
2/2 ━━━━━━━━━━━━━━━━━━━━ 0s 29ms/step - loss: 4.9837
Epoch 16/400
2/2 ━━━━━━━━━

/usr/local/lib/python3.12/dist-packages/keras/src/layers/core/dense.py:93: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(activity_regularizer=activity_regularizer, **kwargs)


2/2 ━━━━━━━━━━━━━━━━━━━━ 3s 29ms/step - loss: 2.0331
Epoch 2/400
2/2 ━━━━━━━━━━━━━━━━━━━━ 0s 27ms/step - loss: 1.7631
Epoch 3/400
2/2 ━━━━━━━━━━━━━━━━━━━━ 0s 34ms/step - loss: 1.9971
Epoch 4/400
2/2 ━━━━━━━━━━━━━━━━━━━━ 0s 28ms/step - loss: 1.9395
Epoch 5/400
2/2 ━━━━━━━━━━━━━━━━━━━━ 0s 30ms/step - loss: 1.8018
Epoch 6/400
2/2 ━━━━━━━━━━━━━━━━━━━━ 0s 28ms/step - loss: 1.8880
Epoch 7/400
2/2 ━━━━━━━━━━━━━━━━━━━━ 0s 27ms/step - loss: 1.5653
Epoch 8/400
2/2 ━━━━━━━━━━━━━━━━━━━━ 0s 27ms/step - loss: 1.6312
Epoch 9/400
2/2 ━━━━━━━━━━━━━━━━━━━━ 0s 27ms/step - loss: 1.6413
Epoch 10/400
2/2 ━━━━━━━━━━━━━━━━━━━━ 0s 27ms/step - loss: 1.5104
Epoch 11/400
2/2 ━━━━━━━━━━━━━━━━━━━━ 0s 29ms/step - loss: 1.5000
Epoch 12/400
2/2 ━━━━━━━━━━━━━━━━━━━━ 0s 28ms/step - loss: 1.4873
Epoch 13/400
2/2 ━━━━━━━━━━━━━━━━━━━━ 0s 29ms/step - loss: 1.3716
Epoch 14/400
2/2 ━━━━━━━━━━━━━━━━━━━━ 0s 29ms/step - loss: 1.3501
Epoch 15/400
2/2 ━━━━━━━━━━━━━━━━━━━━ 0s 28ms/step - loss: 1.3333
Epoch 16/400
2/2 ━━━━━━━━━━━━━━

...

Epoch 1/400
2/2 ━━━━━━━━━━━━━━━━━━━━ 2s 65ms/step - loss: 17.5847
Epoch 2/400
2/2 ━━━━━━━━━━━━━━━━━━━━ 0s 40ms/step - loss: 16.0730
Epoch 3/400
2/2 ━━━━━━━━━━━━━━━━━━━━ 0s 44ms/step - loss: 15.4337 
Epoch 4/400
2/2 ━━━━━━━━━━━━━━━━━━━━ 0s 43ms/step - loss: 14.3806
Epoch 5/400
2/2 ━━━━━━━━━━━━━━━━━━━━ 0s 42ms/step - loss: 13.9775
Epoch 6/400
2/2 ━━━━━━━━━━━━━━━━━━━━ 0s 41ms/step - loss: 12.7622
Epoch 7/400
2/2 ━━━━━━━━━━━━━━━━━━━━ 0s 73ms/step - loss: 12.0397 
Epoch 8/400
2/2 ━━━━━━━━━━━━━━━━━━━━ 0s 89ms/step - loss: 10.7954
Epoch 9/400
2/2 ━━━━━━━━━━━━━━━━━━━━ 0s 42ms/step - loss: 10.1305 
Epoch 10/400
2/2 ━━━━━━━━━━━━━━━━━━━━ 0s 41ms/step - loss: 9.3618
Epoch 11/400
2/2 ━━━━━━━━━━━━━━━━━━━━ 0s 46ms/step - loss: 8.8865 
Epoch 12/400
2/2 ━━━━━━━━━━━━━━━━━━━━ 0s 40ms/step - loss: 7.8106
Epoch 13/400
2/2 ━━━━━━━━━━━━━━━━━━━━ 0s 41ms/step - loss: 7.3402 
Epoch 14/400
2/2 ━━━━━━━━━━━━━━━━━━━━ 0s 40ms/step - loss: 6.6107
Epoch 15/400
2/2 ━━━━━━━━━━━━━━━━━━━━ 0s 40ms/step - loss: 5.8960
Epoch

/usr/local/lib/python3.12/dist-packages/keras/src/layers/core/dense.py:93: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(activity_regularizer=activity_regularizer, **kwargs)


2/2 ━━━━━━━━━━━━━━━━━━━━ 1s 37ms/step - loss: 5.1385
Epoch 2/400
2/2 ━━━━━━━━━━━━━━━━━━━━ 0s 39ms/step - loss: 4.7955 
Epoch 3/400
2/2 ━━━━━━━━━━━━━━━━━━━━ 0s 38ms/step - loss: 4.4544
Epoch 4/400
2/2 ━━━━━━━━━━━━━━━━━━━━ 0s 39ms/step - loss: 4.5251 
Epoch 5/400
2/2 ━━━━━━━━━━━━━━━━━━━━ 0s 44ms/step - loss: 3.9196 
Epoch 6/400
2/2 ━━━━━━━━━━━━━━━━━━━━ 0s 38ms/step - loss: 3.5708
Epoch 7/400
2/2 ━━━━━━━━━━━━━━━━━━━━ 0s 36ms/step - loss: 3.4060 
Epoch 8/400
2/2 ━━━━━━━━━━━━━━━━━━━━ 0s 38ms/step - loss: 3.9131 
Epoch 9/400
2/2 ━━━━━━━━━━━━━━━━━━━━ 0s 37ms/step - loss: 2.9015 
Epoch 10/400
2/2 ━━━━━━━━━━━━━━━━━━━━ 0s 37ms/step - loss: 3.3279 
Epoch 11/400
2/2 ━━━━━━━━━━━━━━━━━━━━ 0s 37ms/step - loss: 2.9882 
Epoch 12/400
2/2 ━━━━━━━━━━━━━━━━━━━━ 0s 36ms/step - loss: 2.7072 
Epoch 13/400
2/2 ━━━━━━━━━━━━━━━━━━━━ 0s 63ms/step - loss: 2.4903 
Epoch 14/400
2/2 ━━━━━━━━━━━━━━━━━━━━ 0s 40ms/step - loss: 2.0790 
Epoch 15/400
2/2 ━━━━━━━━━━━━━━━━━━━━ 0s 35ms/step - loss: 1.9471 
Epoch 16/400
2/2 ━━

/usr/local/lib/python3.12/dist-packages/keras/src/layers/core/dense.py:93: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(activity_regularizer=activity_regularizer, **kwargs)


2/2 ━━━━━━━━━━━━━━━━━━━━ 1s 38ms/step - loss: 3.1396
Epoch 2/400
2/2 ━━━━━━━━━━━━━━━━━━━━ 0s 36ms/step - loss: 2.6977
Epoch 3/400
2/2 ━━━━━━━━━━━━━━━━━━━━ 0s 37ms/step - loss: 2.2922
Epoch 4/400
2/2 ━━━━━━━━━━━━━━━━━━━━ 0s 36ms/step - loss: 1.8541
Epoch 5/400
2/2 ━━━━━━━━━━━━━━━━━━━━ 0s 38ms/step - loss: 1.7549
Epoch 6/400
2/2 ━━━━━━━━━━━━━━━━━━━━ 0s 35ms/step - loss: 1.6051
Epoch 7/400
2/2 ━━━━━━━━━━━━━━━━━━━━ 0s 36ms/step - loss: 1.4814
Epoch 8/400
2/2 ━━━━━━━━━━━━━━━━━━━━ 0s 37ms/step - loss: 1.6429
Epoch 9/400
2/2 ━━━━━━━━━━━━━━━━━━━━ 0s 53ms/step - loss: 1.5659 
Epoch 10/400
2/2 ━━━━━━━━━━━━━━━━━━━━ 0s 38ms/step - loss: 1.5783
Epoch 11/400
2/2 ━━━━━━━━━━━━━━━━━━━━ 0s 36ms/step - loss: 1.4441
Epoch 12/400
2/2 ━━━━━━━━━━━━━━━━━━━━ 0s 37ms/step - loss: 1.3537 
Epoch 13/400
2/2 ━━━━━━━━━━━━━━━━━━━━ 0s 38ms/step - loss: 1.1938 
Epoch 14/400
2/2 ━━━━━━━━━━━━━━━━━━━━ 0s 39ms/step - loss: 1.2329 
Epoch 15/400
2/2 ━━━━━━━━━━━━━━━━━━━━ 0s 75ms/step - loss: 1.2710 
Epoch 16/400
2/2 ━━━━━━━━━

In [7]:
### Selection of the model based on the cross validation

model = keras.Sequential([layers.Dense(25,activation = "relu", input_shape=(input_size,)),
                              layers.Dense(14,activation = "relu"),
                              layers.Dense(output_size,activation = "softmax")])

model.compile(optimizer="adam",loss="sparse_categorical_crossentropy")

X_train = np.array(X_train)
X_cv = np.array(X_cv)
y_train = np.array(y_train)
y_cv = np.array(y_cv)

history = model.fit(X_train,y_train,epochs=800,batch_size=32)

y_tilde = model.predict(X_cv)
y_guess = np.argmax(y_tilde,axis=1)

print(accuracy_score(y_cv,y_guess))


Epoch 1/800


/usr/local/lib/python3.12/dist-packages/keras/src/layers/core/dense.py:93: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(activity_regularizer=activity_regularizer, **kwargs)


4/4 ━━━━━━━━━━━━━━━━━━━━ 1s 10ms/step - loss: 7.9918
Epoch 2/800
4/4 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step - loss: 6.8441
Epoch 3/800
4/4 ━━━━━━━━━━━━━━━━━━━━ 0s 10ms/step - loss: 6.3448
Epoch 4/800
4/4 ━━━━━━━━━━━━━━━━━━━━ 0s 10ms/step - loss: 5.5079
Epoch 5/800
4/4 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step - loss: 4.5933
Epoch 6/800
4/4 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step - loss: 3.9369
Epoch 7/800
4/4 ━━━━━━━━━━━━━━━━━━━━ 0s 10ms/step - loss: 3.5015 
Epoch 8/800
4/4 ━━━━━━━━━━━━━━━━━━━━ 0s 10ms/step - loss: 3.0375
Epoch 9/800
4/4 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step - loss: 2.5335
Epoch 10/800
4/4 ━━━━━━━━━━━━━━━━━━━━ 0s 10ms/step - loss: 2.2368
Epoch 11/800
4/4 ━━━━━━━━━━━━━━━━━━━━ 0s 10ms/step - loss: 1.8414
Epoch 12/800
4/4 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step - loss: 1.6344 
Epoch 13/800
4/4 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step - loss: 1.3787
Epoch 14/800
4/4 ━━━━━━━━━━━━━━━━━━━━ 0s 10ms/step - loss: 1.2411
Epoch 15/800
4/4 ━━━━━━━━━━━━━━━━━━━━ 0s 10ms/step - loss: 1.1684
Epoch 16/800
4/4 ━━━━━━━━━━━━